In [1]:
#This code is for adaptive GPU usage
import keras.backend as K
cfg = K.tf.ConfigProto()
cfg.gpu_options.allow_growth = True
K.set_session(K.tf.Session(config=cfg))

Using TensorFlow backend.


In [2]:
import warnings
warnings.filterwarnings("ignore")

import os
import nltk
import numpy as np
import pandas as pd
import keras.layers as L
import keras.models as M
from keras.optimizers import Adam, Adamax, Nadam, Adagrad
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier, GradientBoostingClassifier

# Merging Data

In [17]:
data = pd.read_csv('Rogue_Data.csv')
data.head()

Unnamed: 0  queryID    query  \
0           0   361570  lewisia   
1           1   361570  lewisia   
2           2   361570  lewisia   
3           3   361570  lewisia   
4           4   361570  lewisia   

                                            response  label  labelID  \
0  lewisia related specie best known lewisia undo...      0        4   
1  lewisia hardy usda zone several specie availab...      0        8   
2  lewisia noun noun lewisia sense genus western ...      0        7   
3  plant number lewisia native western north amer...      0        0   
4  lewisia cotyledon grow metre ft height width s...      0        9   

   q_word_count  q_char_count  q_avg_word  q_stopwords    ...      \
0             3            15    4.333333            2    ...       
1             3            15    4.333333            2    ...       
2             3            15    4.333333            2    ...       
3             3            15    4.333333            2    ...       
4             3            15    4.333333            2    ...       

   r_subjectivity  rouge-1_f  rouge-1_p  rouge-1_r  rouge-2_f  rouge-2_p  \
0        0.375595   0.033898   0.017241        1.0        0.0        0.0   
1        0.509375   0.048780   0.025000        1.0        0.0        0.0   
2        0.211688   0.044444   0.022727        1.0        0.0        0.0   
3        0.363492   0.046512   0.023810        1.0        0.0        0.0   
4        0.385417   0.060606   0.031250        1.0        0.0        0.0   

   rouge-2_r  rouge-l_f  rouge-l_p  rouge-l_r  
0        0.0   0.017246   0.017241        1.0  
1        0.0   0.025015   0.025000        1.0  
2        0.0   0.022739   0.022727        1.0  
3        0.0   0.023823   0.023810        1.0  
4        0.0   0.031280   0.031250        1.0  

[5 rows x 29 columns]

In [18]:
#pd.merge(df1, df2, on='company')
len(data)

5241560

In [51]:
d = data.drop(columns=['Unnamed: 0']).iloc[:55000].copy(deep = True)

In [52]:
d.columns = ['queryID', 'query', 'response', 'label','labelID',
             'q_word_count', 'q_char_count', 'q_avg_word', 'q_stopwords', 'q_numerics', 
             'r_word_count', 'r_char_count', 'r_avg_word', 'r_stopwords', 'r_numerics',
             'q_polarity', 'q_subjectivity','r_polarity', 'r_subjectivity', 'rogue-1_f', 
             'rogue-1_p', 'rogue-1_r','rogue-2_f', 'rogue-2_p', 'rogue-2_r', 'rogue-l_f', 
             'rogue-l_p', 'rogue-l_r']

## Sampling Data

In [53]:
pos = d[d['label']==1].copy(deep = True)
print(len(pos))
pos.head()

524156


queryID                         query  \
6    361570                       lewisia   
10   390132                   elevation l   
25   372493         preparecall statement   
31   157622            old macho man died   
47    60250  definition corrosion control   

                                             response  label  labelID  \
6   lewisia plant genus named meriwether lewis enc...      1        2   
10  elevation los angeles foot elevation san franc...      1        2   
25  contrast preparedstatement statement doesnt of...      1        4   
31  related content macho man randy savage dead wr...      1        0   
47  corrosion control introduction corrosion contr...      1        6   

    q_word_count  q_char_count  q_avg_word  q_stopwords  q_numerics  \
6              3            15    4.333333            2           0   
10             7            28    3.142857            5           0   
25             4            29    6.500000            2           0   
31             8            34    3.375000            4           0   
47             3            28    8.666667            0           0   

      ...      r_subjectivity  rogue-1_f  rogue-1_p  rogue-1_r  rogue-2_f  \
6     ...            0.066667   0.062500   0.032258   1.000000   0.000000   
10    ...            0.500000   0.090909   0.050000   0.500000   0.000000   
25    ...            0.750000   0.076923   0.041667   0.500000   0.000000   
31    ...            0.425000   0.216216   0.121212   1.000000   0.052632   
47    ...            0.385714   0.133333   0.074074   0.666667   0.058824   

    rogue-2_p  rogue-2_r  rogue-l_f  rogue-l_p  rogue-l_r  
6    0.000000   0.000000   0.032291   0.032258   1.000000  
10   0.000000   0.000000   0.050450   0.050000   0.500000  
25   0.000000   0.000000   0.041932   0.041667   0.500000  
31   0.028571   0.333333   0.092081   0.090909   0.750000  
47   0.031250   0.500000   0.074886   0.074074   0.666667  

[5 rows x 28 columns]

In [54]:
pos = pos.sample(frac=1).reset_index(drop=True)
pos.head()

queryID                          query  \
0     1825  sperm cell formed plant _____   
1   508236    played charles manson movie   
2   201357         milton province canada   
3   498559             medicare advantage   
4   391641                function spleen   

                                            response  label  labelID  \
0  gametogenesis back top gametogenesis process f...      1        1   
1  manson played jeff ward cast manson girl macke...      1        5   
2  milton ontario milton census population town s...      1        7   
3  medicare advantage plan eligibility based elig...      1        7   
4  immune system spleen major function spleen inc...      1        0   

   q_word_count  q_char_count  q_avg_word  q_stopwords  q_numerics    ...      \
0             8            42    4.375000            3           0    ...       
1             7            38    4.571429            3           0    ...       
2             7            36    4.285714            4           0    ...       
3             5            27    4.600000            3           0    ...       
4             7            34    4.000000            5           0    ...       

   r_subjectivity  rogue-1_f  rogue-1_p  rogue-1_r  rogue-2_f  rogue-2_p  \
0        0.173333    0.00001    0.00001    0.00001    0.00001    0.00001   
1        0.400000    0.00001    0.00001    0.00001    0.00001    0.00001   
2        0.250000    0.00001    0.00001    0.00001    0.00001    0.00001   
3        0.583333    0.00001    0.00001    0.00001    0.00001    0.00001   
4        0.400000    0.00001    0.00001    0.00001    0.00001    0.00001   

   rogue-2_r  rogue-l_f  rogue-l_p  rogue-l_r  
0    0.00001    0.00001    0.00001    0.00001  
1    0.00001    0.00001    0.00001    0.00001  
2    0.00001    0.00001    0.00001    0.00001  
3    0.00001    0.00001    0.00001    0.00001  
4    0.00001    0.00001    0.00001    0.00001  

[5 rows x 28 columns]

In [55]:
neg = d[d['label']==0].copy(deep = True)
print(len(neg))
neg.head()

4717404


queryID    query                                           response  label  \
0   361570  lewisia  lewisia related specie best known lewisia undo...      0   
1   361570  lewisia  lewisia hardy usda zone several specie availab...      0   
2   361570  lewisia  lewisia noun noun lewisia sense genus western ...      0   
3   361570  lewisia  plant number lewisia native western north amer...      0   
4   361570  lewisia  lewisia cotyledon grow metre ft height width s...      0   

   labelID  q_word_count  q_char_count  q_avg_word  q_stopwords  q_numerics  \
0        4             3            15    4.333333            2           0   
1        8             3            15    4.333333            2           0   
2        7             3            15    4.333333            2           0   
3        0             3            15    4.333333            2           0   
4        9             3            15    4.333333            2           0   

     ...      r_subjectivity  rogue-1_f  rogue-1_p  rogue-1_r  rogue-2_f  \
0    ...            0.375595   0.033898   0.017241        1.0        0.0   
1    ...            0.509375   0.048780   0.025000        1.0        0.0   
2    ...            0.211688   0.044444   0.022727        1.0        0.0   
3    ...            0.363492   0.046512   0.023810        1.0        0.0   
4    ...            0.385417   0.060606   0.031250        1.0        0.0   

   rogue-2_p  rogue-2_r  rogue-l_f  rogue-l_p  rogue-l_r  
0        0.0        0.0   0.017246   0.017241        1.0  
1        0.0        0.0   0.025015   0.025000        1.0  
2        0.0        0.0   0.022739   0.022727        1.0  
3        0.0        0.0   0.023823   0.023810        1.0  
4        0.0        0.0   0.031280   0.031250        1.0  

[5 rows x 28 columns]

In [56]:
neg = neg.sample(frac=1).reset_index(drop=True)
neg.head()

queryID                            query  \
0    45347  convert wps file microsoft word   
1    70559         disc displacement lumbar   
2   364021       measured elasticity supply   
3    87031                   fob definition   
4   304078                       timur mean   

                                            response  label  labelID  \
0  category document file description wps file fo...      0        9   
1  lumbar intervertebral disc displacement withou...      0        9   
2  method price elasticity supply measured percen...      0        3   
3  fob destination term indicating seller incur d...      0        8   
4  variant timour history temir kazakh languagesc...      0        0   

   q_word_count  q_char_count  q_avg_word  q_stopwords  q_numerics    ...      \
0             6            35    5.000000            1           0    ...       
1             3            24    7.333333            0           0    ...       
2             7            40    4.857143            4           0    ...       
3             2            14    6.500000            0           0    ...       
4             4            20    4.250000            2           0    ...       

   r_subjectivity  rogue-1_f  rogue-1_p  rogue-1_r  rogue-2_f  rogue-2_p  \
0        0.560000    0.00001    0.00001    0.00001    0.00001    0.00001   
1        0.375000    0.00001    0.00001    0.00001    0.00001    0.00001   
2        0.361364    0.00001    0.00001    0.00001    0.00001    0.00001   
3        0.250000    0.00001    0.00001    0.00001    0.00001    0.00001   
4        0.166667    0.00001    0.00001    0.00001    0.00001    0.00001   

   rogue-2_r  rogue-l_f  rogue-l_p  rogue-l_r  
0    0.00001    0.00001    0.00001    0.00001  
1    0.00001    0.00001    0.00001    0.00001  
2    0.00001    0.00001    0.00001    0.00001  
3    0.00001    0.00001    0.00001    0.00001  
4    0.00001    0.00001    0.00001    0.00001  

[5 rows x 28 columns]

In [57]:
ratio = 2
negf =neg[:(len(pos)*ratio)].copy(deep=True)
negf.head()

queryID                            query  \
0    45347  convert wps file microsoft word   
1    70559         disc displacement lumbar   
2   364021       measured elasticity supply   
3    87031                   fob definition   
4   304078                       timur mean   

                                            response  label  labelID  \
0  category document file description wps file fo...      0        9   
1  lumbar intervertebral disc displacement withou...      0        9   
2  method price elasticity supply measured percen...      0        3   
3  fob destination term indicating seller incur d...      0        8   
4  variant timour history temir kazakh languagesc...      0        0   

   q_word_count  q_char_count  q_avg_word  q_stopwords  q_numerics    ...      \
0             6            35    5.000000            1           0    ...       
1             3            24    7.333333            0           0    ...       
2             7            40    4.857143            4           0    ...       
3             2            14    6.500000            0           0    ...       
4             4            20    4.250000            2           0    ...       

   r_subjectivity  rogue-1_f  rogue-1_p  rogue-1_r  rogue-2_f  rogue-2_p  \
0        0.560000    0.00001    0.00001    0.00001    0.00001    0.00001   
1        0.375000    0.00001    0.00001    0.00001    0.00001    0.00001   
2        0.361364    0.00001    0.00001    0.00001    0.00001    0.00001   
3        0.250000    0.00001    0.00001    0.00001    0.00001    0.00001   
4        0.166667    0.00001    0.00001    0.00001    0.00001    0.00001   

   rogue-2_r  rogue-l_f  rogue-l_p  rogue-l_r  
0    0.00001    0.00001    0.00001    0.00001  
1    0.00001    0.00001    0.00001    0.00001  
2    0.00001    0.00001    0.00001    0.00001  
3    0.00001    0.00001    0.00001    0.00001  
4    0.00001    0.00001    0.00001    0.00001  

[5 rows x 28 columns]

In [58]:
len(pos)

524156

In [59]:
comb = [pos,negf]
d = pd.concat(comb)
print(len(d))
d.head()

1572468


queryID                          query  \
0     1825  sperm cell formed plant _____   
1   508236    played charles manson movie   
2   201357         milton province canada   
3   498559             medicare advantage   
4   391641                function spleen   

                                            response  label  labelID  \
0  gametogenesis back top gametogenesis process f...      1        1   
1  manson played jeff ward cast manson girl macke...      1        5   
2  milton ontario milton census population town s...      1        7   
3  medicare advantage plan eligibility based elig...      1        7   
4  immune system spleen major function spleen inc...      1        0   

   q_word_count  q_char_count  q_avg_word  q_stopwords  q_numerics    ...      \
0             8            42    4.375000            3           0    ...       
1             7            38    4.571429            3           0    ...       
2             7            36    4.285714            4           0    ...       
3             5            27    4.600000            3           0    ...       
4             7            34    4.000000            5           0    ...       

   r_subjectivity  rogue-1_f  rogue-1_p  rogue-1_r  rogue-2_f  rogue-2_p  \
0        0.173333    0.00001    0.00001    0.00001    0.00001    0.00001   
1        0.400000    0.00001    0.00001    0.00001    0.00001    0.00001   
2        0.250000    0.00001    0.00001    0.00001    0.00001    0.00001   
3        0.583333    0.00001    0.00001    0.00001    0.00001    0.00001   
4        0.400000    0.00001    0.00001    0.00001    0.00001    0.00001   

   rogue-2_r  rogue-l_f  rogue-l_p  rogue-l_r  
0    0.00001    0.00001    0.00001    0.00001  
1    0.00001    0.00001    0.00001    0.00001  
2    0.00001    0.00001    0.00001    0.00001  
3    0.00001    0.00001    0.00001    0.00001  
4    0.00001    0.00001    0.00001    0.00001  

[5 rows x 28 columns]

In [60]:
d = d.sample(frac=1).reset_index(drop=True)
d.head()

queryID                           query  \
0    38562  cast million dollar listing la   
1   267788          cause rside chest pain   
2    36756                 regain collagen   
3   231745              longest cave world   
4    37777        canine blindness symptom   

                                            response  label  labelID  \
0  million dollar listing los angeles anywhere wa...      0        3   
1  chest pain symptom heart attack type chest pai...      0        2   
2  one best way retain collagen protect skin sun ...      0        6   
3  centered green river tributary nolin river fee...      0        8   
4  symptom sard dog prior blindness many dog show...      0        8   

   q_word_count  q_char_count  q_avg_word  q_stopwords  q_numerics    ...      \
0             6            33    4.666667            1           0    ...       
1             5            29    5.000000            1           0    ...       
2             5            28    4.800000            3           0    ...       
3             6            29    4.000000            3           0    ...       
4             3            25    7.666667            0           0    ...       

   r_subjectivity  rogue-1_f  rogue-1_p  rogue-1_r  rogue-2_f  rogue-2_p  \
0        0.775000    0.00001    0.00001    0.00001    0.00001    0.00001   
1        0.033333    0.00001    0.00001    0.00001    0.00001    0.00001   
2        0.425000    0.00001    0.00001    0.00001    0.00001    0.00001   
3        0.400000    0.00001    0.00001    0.00001    0.00001    0.00001   
4        0.166667    0.00001    0.00001    0.00001    0.00001    0.00001   

   rogue-2_r  rogue-l_f  rogue-l_p  rogue-l_r  
0    0.00001    0.00001    0.00001    0.00001  
1    0.00001    0.00001    0.00001    0.00001  
2    0.00001    0.00001    0.00001    0.00001  
3    0.00001    0.00001    0.00001    0.00001  
4    0.00001    0.00001    0.00001    0.00001  

[5 rows x 28 columns]

# Data Loading

In [61]:
features = ['q_word_count', 'q_char_count', 'q_avg_word', 'r_word_count', 
        'r_char_count', 'r_avg_word', 'q_polarity', 'q_subjectivity',
       'r_polarity', 'r_subjectivity']#, 'rogue-1_f', 'rogue-1_p', 'rogue-1_r',
        #'rogue-2_f', 'rogue-2_p', 'rogue-2_r', 'rogue-l_f', 'rogue-l_p', 'rogue-l_r']

split = int(10*((d.shape[0]*0.7)//10))
print(split)

1100720


In [62]:
y = d['label']
x = d[features]

x_train, x_test = x.values[:split,:], x.values[split:,:]
y_train, y_test = y.values[:split], y.values[split:]

In [63]:
x_train.shape, y_train.shape, x_test.shape, y_test.shape

((1100720, 10), (1100720,), (471748, 10), (471748,))

In [72]:
class_ratio = [{0: 9 , 1:1},{0: 9 , 1:1}]

# Tree Based Classifier Models

In [33]:
hyperparams = {
    "trees":{
        "criterions" : ["gini","entropy"],
        "max_depth" : [3,4,5,6,7,8,9,10],
        "max_features": ["log2","sqrt","auto"], 
        "n_estimators": [20,40,60,80,100]}, 
    "gbc":{
        "loss" : ["deviance","exponential"],
        "learning_rate" : [0.1,0.5,0.8,1.0],
        "n_estimators" : [20,40,60,80,100],
        "max_features" : ["log2","sqrt","auto"],
        "max_depth" : [3,4,5,6,7,8,9,10]},
    "nn":{
        "learning_rate" : [0.1,0.01,0.05,0.001,0.005],
        "optim" : ["Adam","Adamax","Adagrad","Nadam"], 
        "activation": ["tanh","sigmoid","relu","linear"]}
}

In [34]:
results = {}
results['RFC'] = {}

for cr in hyperparams["trees"]["criterions"]:
    results['RFC'][str(cr)] = {}
    for dep in hyperparams["trees"]["max_depth"]:
        results['RFC'][str(cr)][str(dep)] = {}
        for feat in hyperparams["trees"]["max_features"]:
            results['RFC'][str(cr)][str(dep)][str(feat)] = {}
            for est in hyperparams["trees"]["n_estimators"]:
                results['RFC'][str(cr)][str(dep)][str(feat)][str(est)] = {}
                print("Hyperparameters used")
                print("Criterion : ",cr)
                print("Maximum Depth : ",dep)
                print("Maximum Features : ",feat)
                print("Number of Estimators : ",est)
                model = RandomForestClassifier(n_estimators=est,
                                              criterion=cr,
                                              max_features=feat,
                                              max_depth=dep,
                                              verbose=3,
                                              class_weight="balanced")
                
                model.fit(x_train,y_train)
                y_pred = model.predict(x_test)
                imp = model.feature_importances_
                score = model.score(x_test,y_test)
                print(score)
                results['RFC'][str(cr)][str(dep)][str(feat)][str(est)]["score"] = score
                
                f = pd.DataFrame(np.column_stack((features,imp)))
                f.columns = ['feature','importance']
                print(f.sort_values(by=['importance'],ascending=False))
                results['RFC'][str(cr)][str(dep)][str(feat)][str(est)]["f_imp"] = f

Hyperparameters used
Criterion :  gini
Maximum Depth :  3
Maximum Features :  log2
Number of Estimators :  20
building tree 1 of 20
building tree 2 of 20
building tree 3 of 20
building tree 4 of 20
building tree 5 of 20
building tree 6 of 20
building tree 7 of 20
building tree 8 of 20


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


building tree 9 of 20
building tree 10 of 20
building tree 11 of 20
building tree 12 of 20
building tree 13 of 20
building tree 14 of 20
building tree 15 of 20
building tree 16 of 20
building tree 17 of 20
building tree 18 of 20
building tree 19 of 20
building tree 20 of 20
0.542060606060606
           feature             importance
12       rogue-1_r     0.3395668742249905
18       rogue-l_r    0.21154710162794294
17       rogue-l_p    0.12299567494222778
16       rogue-l_f    0.08210101243819055
10       rogue-1_f    0.07280596146695312
13       rogue-2_f    0.04267251081014538
15       rogue-2_r    0.04100910366532758
14       rogue-2_p   0.033969414420859025
4     r_char_count     0.0134026795458697
11       rogue-1_p    0.01156162599408844
3     r_word_count   0.007182056547604533
9   r_subjectivity   0.005815803003014089
1     q_char_count    0.00512068586944848
5       r_avg_word  0.0027395023896938627
0     q_word_count   0.002177009720978991
6       q_polarity  0.0019267463705

[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.4s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


building tree 5 of 40
building tree 6 of 40
building tree 7 of 40
building tree 8 of 40
building tree 9 of 40
building tree 10 of 40
building tree 11 of 40
building tree 12 of 40
building tree 13 of 40
building tree 14 of 40
building tree 15 of 40
building tree 16 of 40
building tree 17 of 40
building tree 18 of 40
building tree 19 of 40
building tree 20 of 40
building tree 21 of 40
building tree 22 of 40
building tree 23 of 40
building tree 24 of 40
building tree 25 of 40
building tree 26 of 40
building tree 27 of 40
building tree 28 of 40
building tree 29 of 40
building tree 30 of 40
building tree 31 of 40
building tree 32 of 40
building tree 33 of 40
building tree 34 of 40
building tree 35 of 40
building tree 36 of 40
building tree 37 of 40
building tree 38 of 40
building tree 39 of 40
building tree 40 of 40


...

[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s


building tree 3 of 100
building tree 4 of 100
building tree 5 of 100
building tree 6 of 100
building tree 7 of 100
building tree 8 of 100
building tree 9 of 100
building tree 10 of 100
building tree 11 of 100
building tree 12 of 100
building tree 13 of 100
building tree 14 of 100
building tree 15 of 100
building tree 16 of 100
building tree 17 of 100
building tree 18 of 100
building tree 19 of 100
building tree 20 of 100
building tree 21 of 100
building tree 22 of 100
building tree 23 of 100
building tree 24 of 100
building tree 25 of 100
building tree 26 of 100
building tree 27 of 100
building tree 28 of 100
building tree 29 of 100
building tree 30 of 100
building tree 31 of 100
building tree 32 of 100
building tree 33 of 100
building tree 34 of 100
building tree 35 of 100
building tree 36 of 100
building tree 37 of 100
building tree 38 of 100
building tree 39 of 100
building tree 40 of 100
building tree 41 of 100
building tree 42 of 100
building tree 43 of 100
building tree 44 of 100

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    5.2s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


0.6772121212121213
           feature            importance
12       rogue-1_r   0.12692880437861948
18       rogue-l_r   0.08196977192506384
4     r_char_count   0.07973550374069815
5       r_avg_word   0.07487746956881877
10       rogue-1_f  0.062082054739734396
11       rogue-1_p  0.060096644829328076
9   r_subjectivity   0.05802381954023327
8       r_polarity   0.05765842124960053
3     r_word_count  0.055889816943446524
16       rogue-l_f  0.055135342939737146
2       q_avg_word  0.050298224515514835
17       rogue-l_p    0.0485082764540618
1     q_char_count  0.048207607349596636
14       rogue-2_p  0.025986931912060834
0     q_word_count    0.0255524869085653
15       rogue-2_r  0.023766480163265002
6       q_polarity   0.02359964666421988
13       rogue-2_f   0.02328942546016571
7   q_subjectivity   0.01839327071726985


[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.2s finished


In [11]:
results['ETC'] = {}

for cr in hyperparams["trees"]["criterions"]:
    results['ETC'][str(cr)] = {}
    for dep in hyperparams["trees"]["max_depth"]:
        results['ETC'][str(cr)][str(dep)] = {}
        for feat in hyperparams["trees"]["max_features"]:
            results['ETC'][str(cr)][str(dep)][str(feat)] = {}
            for est in hyperparams["trees"]["n_estimators"]:
                results['ETC'][str(cr)][str(dep)][str(feat)][str(est)] = {}
                print("Hyperparameters used")
                print("Criterion : ",cr)
                print("Maximum Depth : ",dep)
                print("Maximum Features : ",feat)
                print("Number of Estimators : ",est)
                model = ExtraTreesClassifier(n_estimators=est,
                                              criterion=cr,
                                              max_features=feat,
                                              max_depth=dep,
                                              verbose=3,
                                              warm_start=True,
                                              class_weight="balanced")
                
                model.fit(x_train,y_train)
                y_pred = model.predict(x_test)
                imp = model.feature_importances_
                score = model.score(x_test,y_test)
                print(score)
                results['ETC'][str(cr)][str(dep)][str(feat)][str(est)]["score"] = score
                
                f = pd.DataFrame(np.column_stack((features,imp)))
                f.columns = ['feature','importance']
                print(f.sort_values(by=['importance'],ascending=False))
                results['ETC'][str(cr)][str(dep)][str(feat)][str(est)]["f_imp"] = f

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished


Hyperparameters used
Criterion :  gini
Maximum Depth :  3
Maximum Features :  log2
Number of Estimators :  20
building tree 1 of 20
building tree 2 of 20
building tree 3 of 20
building tree 4 of 20
building tree 5 of 20
building tree 6 of 20
building tree 7 of 20
building tree 8 of 20
building tree 9 of 20
building tree 10 of 20
building tree 11 of 20
building tree 12 of 20
building tree 13 of 20
building tree 14 of 20
building tree 15 of 20
building tree 16 of 20
building tree 17 of 20
building tree 18 of 20
building tree 19 of 20
building tree 20 of 20
0.5774545454545454
           feature             importance
12       rogue-1_r     0.4017370459062966
18       rogue-l_r    0.18652660011524977
16       rogue-l_f     0.1113366524857717
15       rogue-2_r    0.10508001829593269
10       rogue-1_f    0.09758542067209125
11       rogue-1_p   0.047029486759398505
17       rogue-l_p   0.020578605065287643
4     r_char_count     0.0106926070770882
14       rogue-2_p  0.0070244398571210785


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s


building tree 1 of 40
building tree 2 of 40
building tree 3 of 40
building tree 4 of 40
building tree 5 of 40
building tree 6 of 40
building tree 7 of 40
building tree 8 of 40
building tree 9 of 40
building tree 10 of 40
building tree 11 of 40
building tree 12 of 40
building tree 13 of 40
building tree 14 of 40
building tree 15 of 40
building tree 16 of 40
building tree 17 of 40
building tree 18 of 40
building tree 19 of 40
building tree 20 of 40
building tree 21 of 40
building tree 22 of 40
building tree 23 of 40
building tree 24 of 40
building tree 25 of 40
building tree 26 of 40
building tree 27 of 40
building tree 28 of 40
building tree 29 of 40
building tree 30 of 40
building tree 31 of 40
building tree 32 of 40
building tree 33 of 40
building tree 34 of 40
building tree 35 of 40
building tree 36 of 40
building tree 37 of 40
building tree 38 of 40
building tree 39 of 40
building tree 40 of 40


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    0.2s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


...

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


building tree 6 of 100
building tree 7 of 100
building tree 8 of 100
building tree 9 of 100
building tree 10 of 100
building tree 11 of 100
building tree 12 of 100
building tree 13 of 100
building tree 14 of 100
building tree 15 of 100
building tree 16 of 100
building tree 17 of 100
building tree 18 of 100
building tree 19 of 100
building tree 20 of 100
building tree 21 of 100
building tree 22 of 100
building tree 23 of 100
building tree 24 of 100
building tree 25 of 100
building tree 26 of 100
building tree 27 of 100
building tree 28 of 100
building tree 29 of 100
building tree 30 of 100
building tree 31 of 100
building tree 32 of 100
building tree 33 of 100
building tree 34 of 100
building tree 35 of 100
building tree 36 of 100
building tree 37 of 100
building tree 38 of 100
building tree 39 of 100
building tree 40 of 100
building tree 41 of 100
building tree 42 of 100
building tree 43 of 100
building tree 44 of 100
building tree 45 of 100
building tree 46 of 100
building tree 47 of 

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    1.3s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


0.574060606060606
           feature            importance
12       rogue-1_r   0.30243046846245286
18       rogue-l_r   0.18360460365842982
15       rogue-2_r   0.07215062729695088
10       rogue-1_f   0.07133088840754781
11       rogue-1_p   0.05539139327443837
17       rogue-l_p    0.0397144294368807
16       rogue-l_f   0.03718216757715134
4     r_char_count   0.03251082153667914
3     r_word_count  0.024111898900224235
14       rogue-2_p  0.022285539532387835
13       rogue-2_f  0.020830900050765787
9   r_subjectivity   0.02077508340179865
0     q_word_count  0.019902870068601187
1     q_char_count   0.01906704414340491
5       r_avg_word  0.018284861914866894
8       r_polarity  0.015923772084969718
2       q_avg_word   0.01559141641540613
7   q_subjectivity   0.01524990487249819
6       q_polarity  0.013661308964545489


[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.2s finished


In [12]:
results['GBC'] = {}

for ls in hyperparams["gbc"]["loss"]:
    results['GBC'][str(ls)] = {}
    for lr in hyperparams["gbc"]["learning_rate"]:
        results['GBC'][str(ls)][str(lr)] = {}
        for est in hyperparams["gbc"]["n_estimators"]:
            results['GBC'][str(ls)][str(lr)][str(est)] = {}
            for feat in hyperparams["gbc"]["max_features"]:
                results['GBC'][str(ls)][str(lr)][str(est)][str(feat)] = {}
                for dep in hyperparams["gbc"]["max_depth"]:
                    results['GBC'][str(ls)][str(lr)][str(est)][str(feat)][str(dep)] = {}
                    print("Hyperparameters used")
                    print("Loss : ",ls)
                    print("Learning rate : ",lr)
                    print("Number of Estimators : ",est)
                    print("Maximum Features : ",feat)
                    print("Maximum Depth : ",dep)
                    model = GradientBoostingClassifier(loss=ls,
                                                       learning_rate=lr,
                                                       n_estimators=est,
                                                       max_features=feat,
                                                       max_depth=dep,
                                                       verbose=3)

                    model.fit(x_train,y_train)
                    y_pred = model.predict(x_test)
                    imp = model.feature_importances_
                    score = model.score(x_test,y_test)
                    print(score)
                    results['GBC'][str(ls)][str(lr)][str(est)][str(feat)][str(dep)]["score"] = score

                    f = pd.DataFrame(np.column_stack((features,imp)))
                    f.columns = ['feature','importance']
                    print(f.sort_values(by=['importance'],ascending=False))
                    results['GBC'][str(ls)][str(lr)][str(est)][str(feat)][str(dep)]["f_imp"] = f

Hyperparameters used
Loss :  deviance
Learning rate :  0.1
Number of Estimators :  20
Maximum Features :  log2
Maximum Depth :  3
      Iter       Train Loss   Remaining Time 
         1           0.6465            0.29s
         2           0.6421            0.30s
         3           0.6378            0.27s
         4           0.6346            0.26s
         5           0.6320            0.24s
         6           0.6294            0.22s
         7           0.6272            0.20s
         8           0.6253            0.19s
         9           0.6235            0.17s
        10           0.6221            0.15s
        11           0.6212            0.14s
        12           0.6199            0.12s
        13           0.6188            0.10s
        14           0.6182            0.09s
        15           0.6172            0.07s
        16           0.6166            0.06s
        17           0.6160            0.04s
        18           0.6152            0.03s
        19    

        12           0.5865            0.45s
        13           0.5836            0.40s
        14           0.5807            0.34s
        15           0.5786            0.28s
        16           0.5765            0.22s
        17           0.5744            0.17s
        18           0.5723            0.11s
        19           0.5695            0.05s
        20           0.5678            0.00s
0.8999393939393939
           feature            importance
12       rogue-1_r   0.10490121403080857
4     r_char_count   0.09741034105734032
18       rogue-l_r   0.07341442701497065
5       r_avg_word    0.0720752684236416
8       r_polarity   0.06986519259736428
3     r_word_count   0.06707780409720954
11       rogue-1_p   0.06554194032388835
10       rogue-1_f   0.06457646338066703
9   r_subjectivity   0.06257968171859307
2       q_avg_word   0.04622777343512611
17       rogue-l_p  0.045677176929424294
16       rogue-l_f  0.044195461832304536
1     q_char_count   0.04374642805722009
13

         2           0.6393            0.36s
         3           0.6350            0.35s
         4           0.6320            0.33s
         5           0.6293            0.31s
         6           0.6267            0.29s
         7           0.6244            0.27s
         8           0.6224            0.25s
         9           0.6206            0.23s
        10           0.6187            0.20s
        11           0.6173            0.18s
        12           0.6159            0.16s
        13           0.6146            0.14s
        14           0.6135            0.12s
        15           0.6124            0.10s
        16           0.6116            0.08s
        17           0.6106            0.06s
        18           0.6098            0.04s
        19           0.6092            0.02s
        20           0.6085            0.00s
0.9
           feature             importance
12       rogue-1_r    0.24578027149061543
18       rogue-l_r     0.1132671041403843
11       rogue-

        16           0.5516            0.31s
        17           0.5491            0.23s
        18           0.5462            0.16s
        19           0.5432            0.08s
        20           0.5404            0.00s
0.8998181818181819
           feature            importance
12       rogue-1_r   0.09725185946677364
4     r_char_count   0.09194755427189785
5       r_avg_word   0.08847941542940216
8       r_polarity   0.07157371850222481
9   r_subjectivity   0.07022897070861045
3     r_word_count   0.06828199946905165
18       rogue-l_r   0.06241521344007987
10       rogue-1_f  0.058161513753389814
1     q_char_count  0.051293807718583606
11       rogue-1_p   0.05035211071038344
2       q_avg_word   0.04951016647229091
17       rogue-l_p   0.04515821094788202
16       rogue-l_f  0.041623000519490014
14       rogue-2_p  0.037294857242669725
13       rogue-2_f   0.02631852039344982
6       q_polarity  0.025908859467688533
0     q_word_count  0.022135022651577286
15       rogue-2_r

         2           0.6362            1.68s
         3           0.6312            1.58s
         4           0.6270            1.50s
         5           0.6234            1.42s
         6           0.6200            1.34s
         7           0.6169            1.24s
         8           0.6143            1.14s
         9           0.6119            1.04s
        10           0.6099            0.94s
        11           0.6080            0.85s
        12           0.6062            0.75s
        13           0.6048            0.65s
        14           0.6034            0.56s
        15           0.6020            0.46s
        16           0.6007            0.37s
        17           0.5994            0.28s
        18           0.5983            0.18s
        19           0.5972            0.09s
        20           0.5964            0.00s
0.8998181818181819
           feature            importance
12       rogue-1_r    0.3851538192033745
4     r_char_count   0.11487147677121992
5  

...

        29           0.5226            3.78s
        30           0.5215            3.75s
        31           0.5199            3.73s
        32           0.5182            3.70s
        33           0.5170            3.63s
        34           0.5164            3.56s
        35           0.5148            3.53s
        36           0.5141            3.45s
        37           0.5128            3.39s
        38           0.5120            3.32s
        39           0.5108            3.26s
        40           0.5094            3.21s
        41           0.5082            3.15s
        42           0.5065            3.09s
        43           0.5053            3.03s
        44           0.5041            2.97s
        45           0.5027            2.92s
        46           0.5019            2.85s
        47           0.5008            2.79s
        48           0.4997            2.73s
        49           0.4990            2.67s
        50           0.4986            2.61s
        51

        90           0.3771            0.77s
        91           0.3757            0.69s
        92           0.3745            0.62s
        93           0.3735            0.54s
        94           0.3714            0.46s
        95           0.3698            0.39s
        96           0.3678            0.31s
        97           0.3661            0.23s
        98           0.3645            0.15s
        99           0.3628            0.08s
       100           0.3611            0.00s
0.8869090909090909
           feature            importance
5       r_avg_word    0.1507963650115843
8       r_polarity     0.130702460819686
9   r_subjectivity   0.10626372558291391
4     r_char_count   0.09011023249528258
2       q_avg_word   0.06291794865941913
3     r_word_count   0.06150290683424472
16       rogue-l_f  0.056732738710201985
1     q_char_count   0.04699858975042075
6       q_polarity   0.03392613014352788
11       rogue-1_p   0.03349772137564246
13       rogue-2_f  0.0333269525631

        27           0.3890           11.58s
        28           0.3848           11.40s
        29           0.3777           11.36s
        30           0.3730           11.21s
        31           0.3688           11.02s
        32           0.3629           10.86s
        33           0.3558           10.74s
        34           0.3509           10.55s
        35           0.3462           10.38s
        36           0.3439           10.15s
        37           0.3394            9.97s
        38           0.3342            9.81s
        39           0.3312            9.60s
        40           0.3267            9.47s
        41           0.3237            9.28s
        42           0.3176            9.16s
        43           0.3129            9.01s
        44           0.3083            8.87s
        45           0.3026            8.73s
        46           0.2994            8.58s
        47           0.2962            8.40s
        48           0.2942            8.23s
        49

        87           0.0829            2.94s
        88           0.0807            2.72s
        89           0.0780            2.50s
        90           0.0750            2.28s
        91           0.0735            2.05s
        92           0.0716            1.82s
        93           0.0693            1.60s
        94           0.0680            1.37s
        95           0.0668            1.14s
        96           0.0653            0.91s
        97           0.0642            0.68s
        98           0.0628            0.45s
        99           0.0612            0.23s
       100           0.0602            0.00s
0.8826666666666667
           feature            importance
5       r_avg_word   0.14083389799011883
8       r_polarity   0.12657704280816323
9   r_subjectivity   0.12345049962548858
4     r_char_count   0.09473619529342756
2       q_avg_word     0.078123959000507
1     q_char_count   0.05832010781110947
16       rogue-l_f   0.04970539065292031
3     r_word_count   0.

        24           0.1932           33.02s
        25           0.1863           32.57s
        26           0.1735           32.50s
        27           0.1620           32.35s
        28           0.1505           32.20s
        29           0.1403           32.01s
        30           0.1345           31.47s
        31           0.1257           31.33s
        32           0.1201           30.81s
        33           0.1149           30.21s
        34           0.1088           29.94s
        35           0.1046           29.43s
        36           0.0980           29.08s
        37           0.0906           28.83s
        38           0.0844           28.51s
        39           0.0804           28.06s
        40           0.0775           27.44s
        41           0.0730           26.97s
        42           0.0692           26.61s
        43           0.0661           26.05s
        44           0.0628           25.62s
        45           0.0613           24.96s
        46

In [15]:
# tree models tabulation
columns = ["model type","criterion","learning rate","max features","max depth","# of estimators","score"]
l = []
for mdl in results.keys():
    if(mdl != "GBC"):
        for crt in results[mdl].keys():
            for mfeat in results[mdl][crt].keys():
                for mdep in results[mdl][crt][mfeat].keys():
                    for nest in results[mdl][crt][mfeat][mdep].keys():
                        score = results[mdl][crt][mfeat][mdep][nest]["score"]
                        l.append([mdl,crt,None,mfeat,mdep,nest,score])
    else:
        for crt in results[mdl].keys():
            for lr in results[mdl][crt].keys():
                for nest in results[mdl][crt][lr].keys():
                    for mfeat in results[mdl][crt][lr][nest].keys():
                        for mdep in results[mdl][crt][lr][nest][mfeat].keys():
                            score = results[mdl][crt][lr][nest][mfeat][mdep]["score"]
                            l.append([mdl,crt,lr,mfeat,mdep,nest,score])

In [21]:
res = pd.DataFrame(l,columns=columns)
res = res.sort_values(by=['score'],ascending=False).reset_index(drop=True)

In [22]:
res.to_csv("Tree_Hyper.csv",sep=',',index=None)

In [40]:
rs=pd.read_csv("Tree_Hyper.csv")

In [41]:
rs

model type    criterion  learning rate max features max depth  \
0           GBC  exponential            0.1         log2         7   
1           GBC  exponential            0.1         auto        10   
2           GBC  exponential            0.1         log2         4   
3           GBC  exponential            0.1         sqrt         7   
4           GBC  exponential            0.1         log2         4   
5           GBC  exponential            0.1         log2         3   
6           GBC  exponential            0.1         auto         9   
7           GBC  exponential            0.1         auto         8   
8           GBC  exponential            0.1         auto         7   
9           GBC  exponential            0.1         auto         6   
10          GBC  exponential            0.1         auto         5   
11          GBC  exponential            0.1         auto         4   
12          GBC  exponential            0.1         auto         3   
13          GBC  exponential            0.1         sqrt        10   
14          GBC  exponential            0.1         sqrt         9   
15          GBC  exponential            0.1         sqrt         8   
16          GBC  exponential            0.1         sqrt         6   
17          GBC     deviance            0.1         sqrt         4   
18          GBC  exponential            0.1         sqrt         5   
19          GBC  exponential            0.1         sqrt         4   
20          GBC  exponential            0.1         sqrt         3   
21          GBC  exponential            0.1         log2        10   
22          GBC  exponential            0.1         log2         9   
23          GBC  exponential            0.1         log2         8   
24          GBC  exponential            0.1         log2         7   
25          GBC  exponential            0.1         log2         6   
26          GBC  exponential            0.1         log2         5   
27          GBC  exponential            0.1         log2         3   
28          GBC     deviance            0.1         log2         3   
29          GBC     deviance            0.1         log2         4   
...         ...          ...            ...          ...       ...   
1410        RFC      entropy            NaN            4      log2   
1411        RFC      entropy            NaN            3      log2   
1412        ETC         gini            NaN            6      sqrt   
1413        RFC      entropy            NaN            3      sqrt   
1414        RFC      entropy            NaN            4      auto   
1415        RFC      entropy            NaN            4      sqrt   
1416        ETC         gini            NaN            4      log2   
1417        RFC         gini            NaN            3      log2   
1418        RFC         gini            NaN            3      log2   
1419        RFC      entropy            NaN            4      sqrt   
1420        RFC      entropy            NaN            3      auto   
1421        RFC         gini            NaN            3      sqrt   
1422        RFC      entropy            NaN            3      log2   
1423        RFC         gini            NaN            3      sqrt   
1424        RFC      entropy            NaN            3      sqrt   
1425        RFC         gini            NaN            3      auto   
1426        RFC      entropy            NaN            3      auto   
1427        RFC      entropy            NaN            3      log2   
1428        RFC      entropy            NaN            4      auto   
1429        RFC         gini            NaN            4      auto   
1430        RFC      entropy            NaN            3      log2   
1431        RFC      entropy            NaN            3      auto   
1432        ETC         gini            NaN            3      auto   
1433        RFC      entropy            NaN            3      sqrt   
1434        RFC      entropy            NaN            3      sqrt   
1435        RFC

# Neural Network

In [27]:
results['nn'] = {}
for optim in hyperparams['nn']['optim']:
    results['nn'][str(optim)] = {}
    for lr in hyperparams['nn']['learning_rate']:
        results['nn'][str(optim)][str(lr)] = {}
        for act in hyperparams['nn']['activation']:
            print("Hyperparameter used")
            print("Optimizer : ",optim)
            print("Learning rate : ",lr)
            print("Activation : ",act)
            results['nn'][str(optim)][str(lr)][str(act)] = {}
            inp = L.Input(shape=(len(features),))
            x = L.Dense(512, activation=act)(inp)
            x = L.Dense(256, activation=act)(x)
            x = L.Dense(128, activation=act)(x)
            x = L.Dense(128, activation=act)(x)
            x = L.Dense(64, activation=act)(x)
            out = L.Dense(1, activation="sigmoid")(x)
            
            model = M.Model(inputs=[inp],outputs=[out])
            model.summary()
            if optim == "Adam":
                o = Adam(lr)
            elif optim == "Adagrad":
                o = Adagrad(lr)
            elif optim == "Adamax":
                o = Adamax(lr)
            elif optim == "Nadam":
                o = Nadam(lr)
            model.compile(o,loss='binary_crossentropy',metrics=['accuracy'])
            
            model.fit(x_train,y_train,epochs=10)
            score = model.evaluate(x_test,y_test)
            y_pred = model.predict(x_test)
            
            results['nn'][str(optim)][str(lr)][str(act)]["score"] = score

Hyperparameter used
Optimizer :  Adam
Learning rate :  0.1
Activation :  tanh
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_4 (InputLayer)         (None, 19)                0         
_________________________________________________________________
dense_19 (Dense)             (None, 512)               10240     
_________________________________________________________________
dense_20 (Dense)             (None, 256)               131328    
_________________________________________________________________
dense_21 (Dense)             (None, 128)               32896     
_________________________________________________________________
dense_22 (Dense)             (None, 128)               16512     
_________________________________________________________________
dense_23 (Dense)             (None, 64)                8256      
________________________________________________________________

Epoch 1/10
38500/38500 [==============================] - 8s 203us/step - loss: 1.6234 - acc: 0.8993
Epoch 2/10
38500/38500 [==============================] - 7s 181us/step - loss: 1.6118 - acc: 0.9000
Epoch 3/10
38500/38500 [==============================] - 7s 180us/step - loss: 1.6118 - acc: 0.9000
Epoch 4/10
38500/38500 [==============================] - 7s 182us/step - loss: 1.6118 - acc: 0.9000
Epoch 5/10
38500/38500 [==============================] - 7s 183us/step - loss: 1.6118 - acc: 0.9000
Epoch 6/10
38500/38500 [==============================] - 7s 183us/step - loss: 1.6118 - acc: 0.9000
Epoch 7/10
38500/38500 [==============================] - 7s 180us/step - loss: 1.6118 - acc: 0.9000
Epoch 8/10
38500/38500 [==============================] - 7s 181us/step - loss: 1.6118 - acc: 0.9000
Epoch 9/10
38500/38500 [==============================] - 7s 182us/step - loss: 1.6118 - acc: 0.9000
Epoch 10/10
16500/16500 [==============================] - 1s 81us/step
Hyperparameter used

Epoch 1/10
38500/38500 [==============================] - 9s 225us/step - loss: 1.6131 - acc: 0.8992
Epoch 2/10
38500/38500 [==============================] - 7s 194us/step - loss: 1.6118 - acc: 0.9000
Epoch 3/10
38500/38500 [==============================] - 7s 195us/step - loss: 1.6118 - acc: 0.9000
Epoch 4/10
38500/38500 [==============================] - 7s 192us/step - loss: 1.6118 - acc: 0.9000
Epoch 5/10
38500/38500 [==============================] - 7s 190us/step - loss: 1.6118 - acc: 0.9000
Epoch 6/10
38500/38500 [==============================] - 8s 196us/step - loss: 1.6118 - acc: 0.9000
Epoch 7/10
38500/38500 [==============================] - 7s 192us/step - loss: 1.6118 - acc: 0.9000
Epoch 8/10
38500/38500 [==============================] - 8s 196us/step - loss: 1.6118 - acc: 0.9000
Epoch 9/10
38500/38500 [==============================] - 7s 194us/step - loss: 1.6118 - acc: 0.9000
Epoch 10/10
16500/16500 [==============================] - 2s 101us/step
Hyperparameter use

Epoch 1/10
38500/38500 [==============================] - 10s 249us/step - loss: 0.3280 - acc: 0.9000
Epoch 2/10
38500/38500 [==============================] - 8s 198us/step - loss: 0.3263 - acc: 0.9000
Epoch 3/10
38500/38500 [==============================] - 8s 202us/step - loss: 0.3259 - acc: 0.9000
Epoch 4/10
38500/38500 [==============================] - 8s 200us/step - loss: 0.3259 - acc: 0.9000
Epoch 5/10
38500/38500 [==============================] - 8s 200us/step - loss: 0.3261 - acc: 0.9000
Epoch 6/10
38500/38500 [==============================] - 8s 199us/step - loss: 0.3261 - acc: 0.9000
Epoch 7/10
38500/38500 [==============================] - 8s 204us/step - loss: 0.3259 - acc: 0.9000
Epoch 8/10
38500/38500 [==============================] - 8s 195us/step - loss: 0.3257 - acc: 0.9000
Epoch 9/10
38500/38500 [==============================] - 8s 198us/step - loss: 0.3260 - acc: 0.9000
Epoch 10/10
16500/16500 [==============================] - 2s 129us/step
Hyperparameter us

Epoch 1/10
38500/38500 [==============================] - 10s 259us/step - loss: 0.3290 - acc: 0.8989
Epoch 2/10
38500/38500 [==============================] - 7s 186us/step - loss: 0.3274 - acc: 0.9000
Epoch 3/10
38500/38500 [==============================] - 7s 191us/step - loss: 0.3269 - acc: 0.9000
Epoch 4/10
38500/38500 [==============================] - 7s 194us/step - loss: 0.3277 - acc: 0.9000
Epoch 5/10
38500/38500 [==============================] - 7s 187us/step - loss: 0.3275 - acc: 0.9000
Epoch 6/10
38500/38500 [==============================] - 7s 188us/step - loss: 0.3276 - acc: 0.9000
Epoch 7/10
38500/38500 [==============================] - 7s 191us/step - loss: 0.3276 - acc: 0.9000
Epoch 8/10
38500/38500 [==============================] - 7s 188us/step - loss: 0.3278 - acc: 0.9000
Epoch 9/10
38500/38500 [==============================] - 7s 182us/step - loss: 0.3286 - acc: 0.9000
Epoch 10/10
16500/16500 [==============================] - 3s 154us/step
Hyperparameter us

...

Epoch 10/10
16500/16500 [==============================] - 5s 318us/step
Hyperparameter used
Optimizer :  Nadam
Learning rate :  0.1
Activation :  linear
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_67 (InputLayer)        (None, 19)                0         
_________________________________________________________________
dense_397 (Dense)            (None, 512)               10240     
_________________________________________________________________
dense_398 (Dense)            (None, 256)               131328    
_________________________________________________________________
dense_399 (Dense)            (None, 128)               32896     
_________________________________________________________________
dense_400 (Dense)            (None, 128)               16512     
_________________________________________________________________
dense_401 (Dense)            (None, 64)               

Epoch 1/10
38500/38500 [==============================] - 19s 504us/step - loss: 14.3365 - acc: 0.1007
Epoch 2/10
38500/38500 [==============================] - 10s 270us/step - loss: 14.3481 - acc: 0.1000
Epoch 3/10
38500/38500 [==============================] - 11s 276us/step - loss: 14.3481 - acc: 0.1000
Epoch 4/10
38500/38500 [==============================] - 11s 274us/step - loss: 14.3481 - acc: 0.1000
Epoch 5/10
38500/38500 [==============================] - 11s 278us/step - loss: 14.3481 - acc: 0.1000
Epoch 6/10
38500/38500 [==============================] - 10s 271us/step - loss: 14.3481 - acc: 0.1000
Epoch 7/10
38500/38500 [==============================] - 10s 269us/step - loss: 14.3481 - acc: 0.1000
Epoch 8/10
38500/38500 [==============================] - 11s 275us/step - loss: 14.3481 - acc: 0.1000
Epoch 9/10
38500/38500 [==============================] - 10s 273us/step - loss: 14.3481 - acc: 0.1000
Epoch 10/10
16500/16500 [==============================] - 6s 338us/step


Epoch 10/10
16500/16500 [==============================] - 6s 349us/step
Hyperparameter used
Optimizer :  Nadam
Learning rate :  0.05
Activation :  relu
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_74 (InputLayer)        (None, 19)                0         
_________________________________________________________________
dense_439 (Dense)            (None, 512)               10240     
_________________________________________________________________
dense_440 (Dense)            (None, 256)               131328    
_________________________________________________________________
dense_441 (Dense)            (None, 128)               32896     
_________________________________________________________________
dense_442 (Dense)            (None, 128)               16512     
_________________________________________________________________
dense_443 (Dense)            (None, 64)                

Epoch 1/10
38500/38500 [==============================] - 21s 545us/step - loss: 0.3274 - acc: 0.9000
Epoch 2/10
38500/38500 [==============================] - 11s 273us/step - loss: 0.3260 - acc: 0.9000
Epoch 3/10
38500/38500 [==============================] - 11s 280us/step - loss: 0.3258 - acc: 0.9000
Epoch 4/10
38500/38500 [==============================] - 11s 277us/step - loss: 0.3255 - acc: 0.9000
Epoch 5/10
38500/38500 [==============================] - 11s 281us/step - loss: 0.3257 - acc: 0.9000
Epoch 6/10
38500/38500 [==============================] - 11s 279us/step - loss: 0.3256 - acc: 0.9000
Epoch 7/10
38500/38500 [==============================] - 11s 279us/step - loss: 0.3251 - acc: 0.9000
Epoch 8/10
38500/38500 [==============================] - 11s 275us/step - loss: 0.3222 - acc: 0.9000
Epoch 9/10
38500/38500 [==============================] - 11s 279us/step - loss: 0.3211 - acc: 0.9000
Epoch 10/10
16500/16500 [==============================] - 6s 354us/step
Hyperpara

16500/16500 [==============================] - 7s 396us/step
Hyperparameter used
Optimizer :  Nadam
Learning rate :  0.005
Activation :  sigmoid
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_81 (InputLayer)        (None, 19)                0         
_________________________________________________________________
dense_481 (Dense)            (None, 512)               10240     
_________________________________________________________________
dense_482 (Dense)            (None, 256)               131328    
_________________________________________________________________
dense_483 (Dense)            (None, 128)               32896     
_________________________________________________________________
dense_484 (Dense)            (None, 128)               16512     
_________________________________________________________________
dense_485 (Dense)            (None, 64)                8256    

In [28]:
# tree models tabulation
columns = ["optimizer","learning rate","activation","score"]
l = []
for mdl in results.keys():
    if(mdl == "nn"):
        for optim in results[mdl].keys():
            for lr in results[mdl][optim].keys():
                for act in results[mdl][optim][lr].keys():
                    score = results[mdl][optim][lr][act]["score"]
                    l.append([optim,lr,act,score])

In [29]:
res = pd.DataFrame(l,columns=columns)
res["loss"] = [s[0] for s in res["score"]]
res["score"] = [s[1] for s in res["score"]]

In [37]:
res = res.sort_values(by=['score'],ascending=False).reset_index(drop=True)

In [38]:
res

optimizer learning rate activation     score       loss
0     Adamax           0.1       tanh  0.900000   0.372951
1       Adam          0.01       tanh  0.900000   0.326380
2      Nadam         0.005    sigmoid  0.900000   0.325357
3       Adam         0.005       tanh  0.900000   0.325704
4     Adamax          0.01    sigmoid  0.900000   0.325749
5    Adagrad          0.05    sigmoid  0.900000   0.325751
6     Adamax           0.1    sigmoid  0.900000   0.325918
7       Adam         0.001    sigmoid  0.900000   0.326029
8     Adamax          0.05    sigmoid  0.900000   0.326290
9     Adamax          0.01       tanh  0.900000   0.327610
10    Adamax         0.005    sigmoid  0.900000   0.325224
11   Adagrad           0.1       tanh  0.900000   0.328433
12    Adamax         0.005       tanh  0.900000   0.328472
13     Nadam          0.01       tanh  0.900000   0.328833
14    Adamax         0.001       relu  0.900000   0.330883
15      Adam          0.05       tanh  0.900000   0.331195
16     Nadam         0.005       tanh  0.900000   0.337000
17      Adam          0.05    sigmoid  0.900000   0.340596
18   Adagrad           0.1    sigmoid  0.900000   0.325284
19      Adam         0.001       relu  0.900000   0.325219
20      Adam           0.1    sigmoid  0.900000   0.357420
21     Nadam         0.001       relu  0.900000   0.313894
22   Adagrad          0.01    sigmoid  0.900000   0.310512
23    Adamax         0.001       tanh  0.900000   0.311233
24    Adamax         0.001    sigmoid  0.900000   0.311382
25   Adagrad          0.01       tanh  0.900000   0.312917
26     Nadam         0.001    sigmoid  0.900000   0.313214
27   Adagrad         0.005    sigmoid  0.900000   0.313363
28   Adagrad         0.001       tanh  0.900000   0.313767
29   Adagrad         0.001    sigmoid  0.900000   0.324701
..       ...           ...        ...       ...        ...
50    Adamax         0.005       relu  0.900000   1.611810
51    Adamax         0.005     linear  0.900000   1.611810
52    Adamax          0.05     linear  0.900000   1.611810
53    Adamax           0.1       relu  0.900000   1.611810
54   Adagrad           0.1     linear  0.900000   1.611810
55      Adam           0.1       relu  0.900000   1.611810
56     Nadam          0.05       relu  0.900000   1.611810
57     Nadam           0.1    sigmoid  0.900000   0.442897
58      Adam         0.005     linear  0.900000   1.611810
59     Nadam          0.01     linear  0.900000   1.611810
60      Adam          0.05       relu  0.900000   1.611810
61     Nadam           0.1     linear  0.900000   1.611810
62      Adam          0.01     linear  0.900000   1.611810
63     Nadam         0.001     linear  0.900000   1.611810
64     Nadam         0.005       relu  0.900000   1.611810
65      Adam           0.1     linear  0.900000   1.611810
66   Adagrad         0.001       relu  0.709515   0.610770
67     Nadam          0.05     linear  0.100000  14.348146
68   Adagrad         0.005     linear  0.100000  14.348146
69    Adamax          0.01     linear  0.100000  14.348146
70   Adagrad          0.01     linear  0.100000  14.348146
71      Adam          0.01       relu  0.100000  14.348146
72   Adagrad         0.005       relu  0.100000  14.348146
73      Adam         0.001     linear  0.100000  14.348146
74      Adam         0.005       relu  0.100000  14.348146
75   Adagrad          0.05     linear  0.100000  14.348146
76      Adam          0.05     linear  0.100000  14.348146
77     Nadam           0.1       relu  0.100000  14.348146
78     Nadam          0.01       relu  0.100000  14.348146
79    Adamax           0.1     linear  0.100000  14.348146

[80 rows x 5 columns]

In [39]:
res.to_csv("NN_Hyper.csv",sep=',',index=None)

# Evaluation Code

In [64]:
tdata = pd.read_csv('Rogue_Test_Data.csv')
#tdata.head()

In [66]:
d2 = tdata.drop(columns=['Unnamed: 0','Unnamed: 0.1']).copy(deep = True)
d2.columns = ['queryID', 'query', 'response','labelID',
             'q_word_count', 'q_char_count', 'q_avg_word', 
             'r_word_count', 'r_char_count', 'r_avg_word',
             'q_polarity', 'q_subjectivity','r_polarity', 'r_subjectivity', 'rogue-1_f', 
             'rogue-1_p', 'rogue-1_r','rogue-2_f', 'rogue-2_p', 'rogue-2_r', 'rogue-l_f', 
             'rogue-l_p', 'rogue-l_r']
#d2.head()

In [33]:
# hyperparams = {
#     "trees":{
#         "criterions" : ["gini","entropy"],
#         "max_depth" : [3,4,5,6,7,8,9,10],
#         "max_features": ["log2","sqrt","auto"], 
#         "n_estimators": [20,40,60,80,100]}, 
#     "gbc":{
#         "loss" : ["deviance","exponential"],
#         "learning_rate" : [0.1,0.5,0.8,1.0],
#         "n_estimators" : [20,40,60,80,100],
#         "max_features" : ["log2","sqrt","auto"],
#         "max_depth" : [3,4,5,6,7,8,9,10]},
#     "nn":{
#         "learning_rate" : [0.1,0.01,0.05,0.001,0.005],
#         "optim" : ["Adam","Adamax","Adagrad","Nadam"], 
#         "activation": ["tanh","sigmoid","relu","linear"]}
# }

In [67]:
x_test_actual = d2[features]

In [68]:
#model type,criterion,learning rate,max features,max depth,# of estimators,score
#GBC,exponential,0.1,log2,7,100,0.900060606060606
#RFC,gini,,10,auto,80,0.6947878787878788
cr = "gini"
#lr = 0.1
est = 100
feat = "auto"
dep = 80
model = RandomForestClassifier(n_estimators=est,criterion=cr,max_features=feat,max_depth=dep,verbose=3,class_weight="balanced_subsample")
#model = GradientBoostingClassifier(loss=ls, learning_rate=lr,n_estimators=est,max_features=feat,max_depth=dep,verbose=3,class_weight=class_ratio)
model.fit(x_train,y_train)
y_pred = model.predict(x_test)
imp = model.feature_importances_
score = model.score(x_test,y_test)
print(score)

building tree 1 of 100


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    7.3s remaining:    0.0s


building tree 2 of 100


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:   14.9s remaining:    0.0s


building tree 3 of 100
building tree 4 of 100
building tree 5 of 100
building tree 6 of 100
building tree 7 of 100
building tree 8 of 100
building tree 9 of 100
building tree 10 of 100
building tree 11 of 100
building tree 12 of 100
building tree 13 of 100
building tree 14 of 100
building tree 15 of 100
building tree 16 of 100
building tree 17 of 100
building tree 18 of 100
building tree 19 of 100
building tree 20 of 100
building tree 21 of 100
building tree 22 of 100
building tree 23 of 100
building tree 24 of 100
building tree 25 of 100
building tree 26 of 100
building tree 27 of 100
building tree 28 of 100
building tree 29 of 100
building tree 30 of 100
building tree 31 of 100
building tree 32 of 100
building tree 33 of 100
building tree 34 of 100
building tree 35 of 100
building tree 36 of 100
building tree 37 of 100
building tree 38 of 100
building tree 39 of 100
building tree 40 of 100
building tree 41 of 100
building tree 42 of 100
building tree 43 of 100
building tree 44 of 100

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed: 12.5min finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.4s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.7s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:   31.6s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.6s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:   29.5s finished


0.6562083993996795


In [ ]:
# optimizer,learning rate,activation,score,loss
# Adamax,0.1,tanh,0.8999999999711008,0.37295132941910714

In [69]:
np.count_nonzero(y_pred == 1)

31847

In [70]:
len(y_pred)

471748

In [71]:
probs = model.predict_proba(x_test_actual)[:,1]

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    7.5s finished


In [72]:
p = []
for i in range(0,d2.shape[0],10):
    l = []
    v = probs[i:i+10].T
    l.append(d2['queryID'][i])
    l.extend(v)
    p.append(l)

In [73]:
result = pd.DataFrame(p)

In [74]:
result.to_csv("answer.tsv",sep='\t',header=None,index=False)